In [119]:
import numpy as np
import pandas as pd
import torch
torch.set_default_tensor_type(torch.FloatTensor) 
import copy
import sys
import os
notebook_dir = os.getcwd()
parent_dir = os.path.dirname(notebook_dir)
# Add the parent directory to the Python path
sys.path.append(parent_dir)

# sys.path.append('/Users/lucile/causal_info_gain/causal_prospective_merge/data')
# sys.path.append('/Users/lucile/causal_info_gain/causal_prospective_merge/data')
from rct_data_generator import *
from outcome_models import *
from plotting_functions import *
from mcmc_bayes_update import *
from eig_comp_utils import *
from research_exp_utils import *

# from econml.metalearners import TLearner
# from sklearn.ensemble import GradientBoostingRegressor, GradientBoostingClassifier


In [120]:
import yaml

In [121]:
with open("/Users/jake/Python/causal_prospective_merge/experiments/twins_ranking_linear/results/05-03 16:44:53/results.metrics.csv", "r") as f:
    results_dict = yaml.safe_load(f)

In [122]:
results_df = pd.DataFrame(results_dict)

In [123]:
results_df.groupby("Method").mean()

precision_at_1  precision_at_10  \
Method                                                            
caus_closed_form                      0.178571         0.550000   
obs_closed_form                       0.214286         0.500000   
random                                0.000000         0.250000   
sample size                           0.000000         0.239286   
similarity_cov_distrib_ranking        0.000000         0.210714   
similarity_pscore_ranking size        0.035714         0.375000   

                                precision_at_20  precision_at_5       rho  \
Method                                                                      
caus_closed_form                       0.762500        0.421429  0.680696   
obs_closed_form                        0.728571        0.342857  0.620377   
random                                 0.478571        0.192857  0.015103   
sample size                            0.473214        0.121429  0.280883   
similarity_cov_distrib_ranking         0.475000        0.078571 -0.101092   
similarity_pscore_ranking size         0.608929        0.214286  0.320839   

                                     tau  
Method                                    
caus_closed_form                0.508242  
obs_closed_form                 0.456044  
random                          0.011905  
sample size                     0.194322  
similarity_cov_distrib_ranking -0.071062  
similarity_pscore_ranking size  0.223810

In [124]:
notebook_dir = os.getcwd()

In [125]:
# from scipy.stats import kendalltau, spearmanr

# def average_precision_at_k(true_rankings, predicted_rankings, k):
#     num_hits = 0
#     sum_precision = 0
#     for i, pred in enumerate(predicted_rankings[:k], 1):
#         if pred in true_rankings:
#             num_hits += 1
#             sum_precision += num_hits / i
#     if not true_rankings:
#         return 0
#     return sum_precision / min(len(true_rankings), k)

# def mean_average_precision(true_rankings, predicted_rankings, k=None):
#     if k is None:
#         k = len(true_rankings)
#     avg_precision = np.mean([average_precision_at_k(true_rankings, predicted_rankings, k_) for k_ in range(1, k + 1)])
#     return avg_precision

# def precision_at_k(true_rankings, predicted_rankings, k):
#     intersection = set(predicted_rankings[:k]) & set(true_rankings[:k])
#     return len(intersection) / k

# def recall_at_k(true_rankings, predicted_rankings, k):
#     intersection = set(predicted_rankings[:k]) & set(true_rankings[:k])
#     return len(intersection) / len(true_rankings)

# def mrr(true_rankings, predicted_rankings):
#     for i, pred in enumerate(predicted_rankings, 1):
#         if pred in true_rankings:
#             return 1 / i
#     return 0

# def ndcg(true_rankings, predicted_rankings, k=None):
#     if k is None:
#         k = len(true_rankings)
#     dcg = sum(2 ** true_rankings[i] - 1 / np.log2(i + 2) for i in range(k))
#     ideal_rankings = sorted(true_rankings, reverse=True)
#     ideal_dcg = sum(2 ** ideal_rankings[i] - 1 / np.log2(i + 2) for i in range(k))
#     return dcg / ideal_dcg

# def compare_to_ground_truth(results_dict, true_cate_ranking, eig_ranking, merged_mse, top_n = None, k = None):
    
#     if top_n is not None:
#         topn_eig_ranking = eig_ranking[:top_n]
#         topn_true_cate_ranking = true_cate_ranking[:top_n]
#         topn_merged_mse = merged_mse[:top_n]
#     else: 
#         topn_eig_ranking, topn_true_cate_ranking,topn_merged_mse = eig_ranking, true_cate_ranking,merged_mse

#     if k is None:
#         k = len(true_cate_ranking)
    
#     implied_ranking = [eig_ranking.index(val) for val in list(range(min(eig_ranking),max(eig_ranking)+1))]
    
#     results_dict['tau'] = results_dict.get('tau',[])+[(kendalltau(implied_ranking, merged_mse)[0])]    
#     results_dict['rho'] = results_dict.get('rho',[])+[(spearmanr(implied_ranking, merged_mse)[0])]  

#     if type(k) == int:
#         results_dict['precision_at_k'] = results_dict.get('precision_at_k',[]) + [precision_at_k(true_cate_ranking, topn_eig_ranking, k"k)]
#     else:
#         for val in k:
#             results_dict['precision_at_'+str(val)] : results_dict.get('precision_at_'+str(val),[]) + [precision_at_k(true_cate_ranking, topn_eig_ranking, k:val)]
#     # results_dict['recall_at_k'].append(recall_at_k(true_cate_ranking, topn_eig_ranking, k=k[0]))
#     # if type(k) == int:
#     #     results_dict['recall_at_k'].append(recall_at_k(true_cate_ranking, topn_eig_ranking, k=k))
#     # else:
#     #     for val in k:
#     #         results_dict['recall_at_'+str(val)].append(recall_at_k(true_cate_ranking, topn_eig_ranking, k=val))
#     # results_dict['mean average precision'].append(mean_average_precision(topn_true_cate_ranking, topn_eig_ranking, k=k[0]))
#     # results_dict['ndcg'].append(ndcg(topn_true_cate_ranking, topn_eig_ranking, k[0]))
#     # results_dict['rank corr eig'].append(np.corrcoef(topn_true_cate_ranking, topn_eig_ranking)[0, 1])
#     # results_dict['mean reciprocal rank'].append(mrr(topn_true_cate_ranking, topn_eig_ranking))

#     return results_dict

In [126]:
path = "../"
data_with_groundtruth, x, t, y = get_data('twins', path)
data_with_groundtruth.dropna(inplace=True)
data_with_groundtruth = data_with_groundtruth.rename(columns={'t': 'T', 'y': 'Y'})
XandT = data_with_groundtruth.drop(columns=['Y','y0','y1','ite'])
XandT.head()

eclamp  gestatcat1  gestatcat2  gestatcat3  gestatcat4  gestatcat5  \
0     0.0         0.0         1.0         1.0         0.0         1.0   
1     0.0         0.0         1.0         1.0         0.0         0.0   
2     0.0         0.0         1.0         0.0         1.0         0.0   
3     0.0         0.0         0.0         0.0         1.0         0.0   
4     0.0         0.0         1.0         1.0         0.0         0.0   

   gestatcat6  gestatcat7  gestatcat8  gestatcat9  ...  brstate_reg  feduc6  \
0         1.0         0.0         0.0         1.0  ...          5.0     2.0   
1         0.0         0.0         1.0         0.0  ...          5.0     5.0   
2         0.0         0.0         0.0         1.0  ...          5.0     2.0   
3         1.0         0.0         0.0         0.0  ...          5.0     4.0   
4         0.0         0.0         0.0         0.0  ...          5.0     4.0   

   dfageq  nprevistq  data_year  crace  birmon  dtotord_min  dlivord_min    T  
0     1.0        0.0        0.0    0.0     0.0          3.0          3.0  1.0  
1     8.0        0.0        0.0    0.0     0.0          1.0          1.0  1.0  
2     0.0        0.0        0.0    0.0     0.0          1.0          1.0  0.0  
3     6.0        0.0        0.0    0.0     0.0          2.0          2.0  1.0  
4     7.0        0.0        0.0    1.0     0.0          3.0          3.0  0.0  

[5 rows x 76 columns]

In [127]:
number_of_candidate_sites = 5

min_sample_size_cand = 150
max_sample_size_cand = 300
host_sample_size = 400 
desired_initial_sample_size = 10**4
XandT = XandT.sample(n=desired_initial_sample_size, replace=True, random_state=42)
added_T_coef = 20 # to increase importance of T

outcome_function = None
std_true_y = 1
power_x = 1
power_x_t = 1
sigma_rand_error = 1
true_beta_great_0_prop = 0.8

exp_parameters = {'number_of_candidate_sites': number_of_candidate_sites+1, 'min_sample_size_cand': min_sample_size_cand, \
                'max_sample_size_cand': max_sample_size_cand, 'host_sample_size': 2000+host_sample_size, 'outcome_function': outcome_function, \
                'std_true_y': std_true_y, 'power_x': power_x, 'power_x_t': power_x_t}

causal_param_first_index = power_x*np.shape(XandT)[1]

In [128]:
def generating_random_sites_from(data, exp_parameters, added_T_coef=1):
    
    candidates = {}
    sample_size, number_covariates = np.shape(data)[0], np.shape(data)[1]
    function_indices = {0: lambda X: np.log(X+1), 1: lambda X: X**3, 2: lambda X: X, 3: lambda X: X**2 }
    number_of_candidate_sites = exp_parameters['number_of_candidate_sites']
    min_sample_size_cand = exp_parameters['min_sample_size_cand']
    max_sample_size_cand = exp_parameters['max_sample_size_cand']
    outcome_function = None
    std_true_y = exp_parameters['std_true_y']
    power_x = exp_parameters['power_x']
    power_x_t = exp_parameters['power_x_t']
    number_features = number_covariates
    created_sites = 0
    
    while created_sites < number_of_candidate_sites:

        np.random.seed(np.random.randint(10000))
        
        selected_features_for_subsampling = np.random.randint(2, size = number_features) 
        # binary bool vector representing selection for being an input of the sampling function
        random_coefs = [np.random.uniform(-10, 10) for _ in range(number_features)] 
        random_fct_idx = [np.random.randint(0, len(function_indices.keys())) for _ in range(number_features)] 
        
        def p_assigned_to_site(X, T, eps):
            result = 0
            for j in range(number_features-1):
                result += selected_features_for_subsampling[j] * random_coefs[j] * function_indices[random_fct_idx[j]](X[j])
            # here i use added_T_coef * random_coefs to increase importance of T
            result +=  added_T_coef * random_coefs[-1] *  function_indices[random_fct_idx[-1]](T) #selected_features_for_subsampling[-1]
            return sigmoid(result + eps)
        
        sample_size = np.random.randint(min_sample_size_cand, max_sample_size_cand + 1)  # Add 1 to include max_sample_size_cand

        if created_sites==0:
            sample_size = exp_parameters['host_sample_size']
        design_data_cand = subsample_one_dataset(XandT, p_assigned_to_site, sample_size, power_x, power_x_t, outcome_function, std_true_y, seed=np.random.randint(10000))
        design_data_cand = design_data_cand.dropna()
        any_nan = design_data_cand.isna().any().any()
        if not design_data_cand.empty and not any_nan: # we're appending
            candidates[created_sites] = design_data_cand
            created_sites += 1
        else:
            pass # not appending
       

    return candidates

In [129]:
#dictionnary of random sites
candidate_sites = generating_random_sites_from(XandT, exp_parameters, added_T_coef=50)

for i, cand in candidate_sites.items():
    candidate_sites[i] = pd.concat([cand, data_with_groundtruth.loc[cand.index, 'Y']], axis=1)

 /var/folders/v1/x4lr48v53397r9xsq4q70mvw0000gn/T/ipykernel_3087/3984761675.py:28: FutureWarning:Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
 /var/folders/v1/x4lr48v53397r9xsq4q70mvw0000gn/T/ipykernel_3087/3984761675.py:28: FutureWarning:Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
 /var/folders/v1/x4lr48v53397r9xsq4q70mvw0000gn/T/ipykernel_3087/3984761675.py:28: FutureWarning:Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
 /var/folders/v1/x4lr48v53397r9xsq4q70mvw0000gn/T/ipykerne

In [130]:
beta = (np.random.randn(152) > true_beta_great_0_prop)
beta = beta - np.mean(beta)

for i, cand in candidate_sites.items():
    candidate_sites[i]["Y"] = candidate_sites[i].drop(columns=["Y"]) @ beta 
    candidate_sites[i]["Y"] += sigma_rand_error * np.random.randn(len(candidate_sites[i]["Y"]))
    

In [131]:
host = candidate_sites[0][:host_sample_size]
XandT_host, Y_host = torch.from_numpy(host.drop(columns=["Y"]).values), torch.from_numpy(host["Y"].values)

host_test = candidate_sites[0][host_sample_size:]
XandT_host_test, Y_host_test = torch.from_numpy(host.drop(columns=["Y"]).values), torch.from_numpy(host["Y"].values)

candidate_sites = {key: value for key, value in candidate_sites.items() if key != 0}



# Prior parameters for Bayesian update on host
d = np.shape(host)[1]-1
prior_mean = torch.zeros(d)
sigma_prior = 1
beta_0, sigma_0_sq, inv_cov_0 = prior_mean, sigma_rand_error,torch.eye(d)
prior_hyperparameters = {'beta_0': beta_0, 'sigma_0_sq': sigma_0_sq,"inv_cov_0":inv_cov_0}

In [132]:
n_samples_outer_expectation_obs = 400
n_samples_inner_expectation_obs = 800
n_samples_outer_expectation_caus = 400
n_samples_inner_expectation_caus = 800

sampling_parameters = {'n_samples_inner_expectation_obs':n_samples_inner_expectation_obs, 'n_samples_outer_expectation_obs':n_samples_outer_expectation_obs, \
                       'n_samples_inner_expectation_caus':n_samples_inner_expectation_caus, 'n_samples_outer_expectation_caus':n_samples_outer_expectation_caus}

eig_results = {"EIG_obs_GP": [], 'EIG_caus_GP':[], "EIG_obs_closed_form":[], "EIG_caus_closed_form":[], "EIG_obs_bart":[], "EIG_caus_bart":[]}

In [133]:
print(f" % treated in host: {round(100 * host['T'].mean(),2)}%")

 % treated in host: 64.25%


In [134]:
for _,candidate in candidate_sites.items():
    print(f"For a sample size of {np.shape(candidate)[0]}")
    print(f" % treated in candidate: {round(100 * candidate['T'].mean(),2)}%")

For a sample size of 222
 % treated in candidate: 61.26%
For a sample size of 235
 % treated in candidate: 83.4%
For a sample size of 249
 % treated in candidate: 76.71%
For a sample size of 280
 % treated in candidate: 38.57%
For a sample size of 189
 % treated in candidate: 26.46%


In [135]:
for _, candidate in candidate_sites.items():
    X_cand = torch.from_numpy(candidate.drop(columns=["Y"]).values)
    bayes_reg = BayesianLinearRegression(prior_hyperparameters)
    bayes_reg.set_causal_index(causal_param_first_index)
    post_host_parameters = bayes_reg.fit(XandT_host, Y_host)
    n_samples = n_samples_outer_expectation_obs * (n_samples_inner_expectation_obs + 1)

    eig_results["EIG_obs_closed_form"].append(
            bayes_reg.closed_form_obs_EIG(X_cand)
            )
    eig_results["EIG_caus_closed_form"].append(
            bayes_reg.closed_form_causal_EIG(X_cand)
            )

In [136]:
# eig_results["EIG_obs_from_samples"]=[]
# eig_results["EIG_caus_from_samples"]=[]

# for i, candidate in candidate_sites.items():
#     print("from samples "+str(i))
#     X_cand = torch.from_numpy(candidate.drop(columns=["Y"]).values)
#     bayes_reg = BayesianLinearRegression(prior_hyperparameters)
#     bayes_reg.set_causal_index(causal_param_first_index)
#     post_host_parameters = bayes_reg.fit(XandT_host, Y_host)

#     eig_results["EIG_obs_from_samples"].append(
#             bayes_reg.samples_obs_EIG(
#                 X_cand, n_samples_outer_expectation_obs, n_samples_inner_expectation_obs
#             )
#         )
#     eig_results["EIG_caus_from_samples"].append(
#             bayes_reg.samples_causal_EIG(
#                 X_cand, n_samples_outer_expectation_obs, n_samples_inner_expectation_obs
#             )
#         )

In [137]:
# now merge and compute some CATE error
merged_datasets = {}

for i, candidate in candidate_sites.items():
    merged_datasets[i]= pd.concat([host, candidate], axis=0)

In [138]:
cate_diff = {}
merged_mse = []
XandT_host_test = host_test.drop(columns=["Y"])

X_zero = XandT_host_test.copy() # we predict on host with T=0 and T=1
X_zero.iloc[:,causal_param_first_index:] = 0

X_one = XandT_host_test.copy()
X_one.iloc[:,causal_param_first_index:] = XandT_host_test.iloc[:,:causal_param_first_index]

### Merging and computing ground truth

In [139]:
data_with_groundtruth

eclamp  gestatcat1  gestatcat2  gestatcat3  gestatcat4  gestatcat5  \
0         0.0         0.0         1.0         1.0         0.0         1.0   
1         0.0         0.0         1.0         1.0         0.0         0.0   
2         0.0         0.0         1.0         0.0         1.0         0.0   
3         0.0         0.0         0.0         0.0         1.0         0.0   
4         0.0         0.0         1.0         1.0         0.0         0.0   
...       ...         ...         ...         ...         ...         ...   
11979     0.0         0.0         1.0         1.0         0.0         0.0   
11980     0.0         0.0         1.0         0.0         1.0         0.0   
11981     0.0         0.0         0.0         0.0         1.0         1.0   
11982     0.0         0.0         1.0         0.0         0.0         1.0   
11983     0.0         1.0         0.0         1.0         1.0         1.0   

       gestatcat6  gestatcat7  gestatcat8  gestatcat9  ...  data_year  crace  \
0             1.0         0.0         0.0         1.0  ...        0.0    0.0   
1             0.0         0.0         1.0         0.0  ...        0.0    0.0   
2             0.0         0.0         0.0         1.0  ...        0.0    0.0   
3             1.0         0.0         0.0         0.0  ...        0.0    0.0   
4             0.0         0.0         0.0         0.0  ...        0.0    1.0   
...           ...         ...         ...         ...  ...        ...    ...   
11979         0.0         0.0         0.0         0.0  ...        2.0    0.0   
11980         0.0         0.0         0.0         0.0  ...        2.0    0.0   
11981         0.0         0.0         0.0         1.0  ...        2.0    0.0   
11982         0.0         0.0         0.0         1.0  ...        2.0    0.0   
11983         0.0         1.0         0.0         1.0  ...        2.0    0.0   

       birmon  dtotord_min  dlivord_min    T    Y   y0   y1  ite  
0         0.0          3.0          3.0  1.0  0.0  1.0  0.0 -1.0  
1         0.0          1.0          1.0  1.0  0.0  1.0  0.0 -1.0  
2         0.0          1.0          1.0  0.0  0.0  0.0  0.0  0.0  
3         0.0          2.0          2.0  1.0  0.0  0.0  0.0  0.0  
4         0.0          3.0          3.0  0.0  1.0  1.0  1.0  0.0  
...       ...          ...          ...  ...  ...  ...  ...  ...  
11979    10.0          6.0          2.0  1.0  0.0  0.0  0.0  0.0  
11980    11.0          1.0          1.0  0.0  0.0  0.0  1.0  1.0  
11981    11.0          2.0          1.0  0.0  0.0  0.0  0.0  0.0  
11982    11.0          3.0          3.0  0.0  0.0  0.0  1.0  1.0  
11983     6.0          1.0          1.0  0.0  0.0  0.0  0.0  0.0  

[11984 rows x 80 columns]

In [140]:
from sklearn.metrics import mean_squared_error
from sklearn.linear_model import Ridge
from sklearn.metrics import log_loss

merged_mse = []

for i, candidate in merged_datasets.items():

    XandT_merged = candidate.drop(columns=["Y"])
    Y_merged = candidate['Y']

    learner = Ridge(fit_intercept=True)
    learner.fit(y=Y_merged, X=XandT_merged) # we fit on merged datasets

    true_cate = (X_one - X_zero) @ beta

    pred_cate = learner.predict(X_one)-learner.predict(X_zero)

    merged_mse.append(mean_squared_error(true_cate, pred_cate))


In [141]:
learner.coef_.max()

1.0862571015537292

### Comparing our EIGs with ground truth

In [142]:
obs_eig_ranking_closed_form = sorted(range(len(eig_results["EIG_obs_closed_form"])), key=lambda i: eig_results["EIG_obs_closed_form"][i], reverse=True)
print(obs_eig_ranking_closed_form)

caus_eig_ranking_closed_form = sorted(range(len(eig_results["EIG_caus_closed_form"])), key=lambda i: eig_results["EIG_caus_closed_form"][i], reverse=True)
print(caus_eig_ranking_closed_form)

# obs_eig_ranking_from_samples = sorted(range(len(eig_results["EIG_obs_from_samples"])), key=lambda i: eig_results["EIG_obs_from_samples"][i], reverse=True)
# print(obs_eig_ranking_from_samples)

# caus_eig_ranking_from_samples = sorted(range(len(eig_results["EIG_caus_from_samples"])), key=lambda i: eig_results["EIG_caus_from_samples"][i], reverse=True)
# print(caus_eig_ranking_from_samples)

true_cate_ranking = sorted(range(len(merged_mse)), key=lambda i: merged_mse[i], reverse=False) # reverse is False because its error terms
print(true_cate_ranking)

[3, 4, 0, 2, 1]
[3, 4, 0, 2, 1]
[0, 3, 4, 2, 1]


In [143]:
true_cate_ranking

[0, 3, 4, 2, 1]

In [144]:
eig_results

{'EIG_obs_GP': [],
 'EIG_caus_GP': [],
 'EIG_obs_closed_form': [29.525043881803782,
  26.241507917969695,
  28.86417022989512,
  39.25597380738497,
  32.434968999432684],
 'EIG_caus_closed_form': [13.277509889220699,
  10.05399132026421,
  11.660204166263345,
  19.28841451878147,
  17.137688299526964],
 'EIG_obs_bart': [],
 'EIG_caus_bart': []}

In [145]:
true_cate_ranking

[0, 3, 4, 2, 1]

In [146]:
merged_mse

[0.4609367551934921,
 0.6479011905381987,
 0.6406365617370391,
 0.5320072075862331,
 0.6044095457778321]

In [147]:
k =[1,3,5]
top_n = None

In [148]:
# correlation_with_true_rankings={'tau':[],'rho':[], \
#       'recall_at_k':[], 'mean average precision': [], \
#       'ndcg': [], 'rank corr eig': [], 'mean reciprocal rank': []}

correlation_with_true_rankings={}

for val in k:
    correlation_with_true_rankings['precision_at_'+str(val)] = []
compare_to_ground_truth(correlation_with_true_rankings, true_cate_ranking, obs_eig_ranking_closed_form, merged_mse=merged_mse, top_n = top_n, k = k)
compare_to_ground_truth(correlation_with_true_rankings, true_cate_ranking, caus_eig_ranking_closed_form,merged_mse=merged_mse, top_n = top_n, k = k)

# compare_to_ground_truth(correlation_with_true_rankings, true_cate_ranking, obs_eig_ranking_from_samples, top_n = top_n, k = k)
# compare_to_ground_truth(correlation_with_true_rankings, true_cate_ranking, caus_eig_ranking_from_samples, top_n = top_n, k = k)


{'precision_at_1': [0.0, 0.0],
 'precision_at_3': [1.0, 1.0],
 'precision_at_5': [1.0, 1.0],
 'tau': [0.6, 0.6],
 'rho': [0.7, 0.7]}

### Baselines

In [149]:
XandT_host = host.drop(columns = ["Y"])

In [150]:
import copy
from sklearn.linear_model import LogisticRegression

### random ranking
random_ranking = np.random.choice(np.arange(1, number_of_candidate_sites+1), size=number_of_candidate_sites, replace=False)


### ranking by sample size
sample_size_order = sorted(candidate_sites.keys(), key=lambda key: -candidate_sites[key].shape[0])


### ranking by similarity of covariate distribution
mean_vector_host = XandT_host.iloc[:,:causal_param_first_index].mean()
cov_matrix_host = XandT_host.iloc[:,:causal_param_first_index].cov()
mvn = multivariate_normal(mean=mean_vector_host, cov=cov_matrix_host, allow_singular=1)
# get log likelihood of candidate sites
log_likelihood_list=[]
for i, candidate in candidate_sites.items():
    log_likelihoods=mvn.logpdf(candidate.iloc[:,:causal_param_first_index].values)
    log_likelihood_list.append(np.mean(log_likelihoods))

similarity_cov_distrib_ranking= sorted(range(len(log_likelihood_list)), key=lambda i: log_likelihood_list[i], reverse=True)

### ranking by similarity of propensity scores
# we fit a propensity score model at target site and store logloss
# for each site: we fit the model further on the cand site and compute log
# nd assess the loss. Sites associated with loss values with higher discrepancy from the host should have distinct 
#treatment allocation scheme, and thus be a better fit. 

ps_model = LogisticRegression(fit_intercept=True)
ps_model.fit(XandT_host.iloc[:,:causal_param_first_index], XandT_host['T'])
t_host_pred = ps_model.predict(XandT_host.iloc[:,:causal_param_first_index])
mse_host = mean_squared_error(t_host_pred, XandT_host['T'])
mse_diff_list = []


for i, candidate in candidate_sites.items():
    # ps_model_copy= copy.deepcopy(ps_model)
    # ps_model_copy.fit(candidate.iloc[:,:causal_param_first_index], candidate['T'])
    t_cand_pred = ps_model.predict(candidate.iloc[:,:causal_param_first_index]) # predict on host!
    mse_cand = abs(mean_squared_error(t_cand_pred, candidate['T']) - mse_host)
    mse_diff_list.append(mse_cand)

similarity_pscore_ranking = sorted(range(len(mse_diff_list)), key=lambda i: mse_diff_list[i], reverse=True) 
# the more diff in pscore the better so reverse=True


print(random_ranking)
print(sample_size_order)
print(similarity_cov_distrib_ranking)
print(similarity_pscore_ranking)

[5 1 3 4 2]
[4, 3, 2, 1, 5]
[1, 2, 4, 0, 3]
[3, 0, 4, 1, 2]


 /Users/jake/Python/causal_prospective_merge/.conda/lib/python3.11/site-packages/sklearn/linear_model/_logistic.py:460: ConvergenceWarning:lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression


In [151]:
compare_to_ground_truth(correlation_with_true_rankings, true_cate_ranking, list(random_ranking),merged_mse=merged_mse, top_n = top_n, k = k)
compare_to_ground_truth(correlation_with_true_rankings, true_cate_ranking, list(sample_size_order),merged_mse=merged_mse, top_n = top_n, k = k)
compare_to_ground_truth(correlation_with_true_rankings, true_cate_ranking, list(similarity_cov_distrib_ranking),merged_mse=merged_mse, top_n = top_n, k = k)
compare_to_ground_truth(correlation_with_true_rankings, true_cate_ranking, list(similarity_pscore_ranking),merged_mse=merged_mse, top_n = top_n, k = k)

{'precision_at_1': [0.0, 0.0, 0.0, 0.0, 0.0, 0.0],
 'precision_at_3': [1.0,
  1.0,
  0.3333333333333333,
  0.6666666666666666,
  0.3333333333333333,
  1.0],
 'precision_at_5': [1.0, 1.0, 0.8, 0.8, 1.0, 1.0],
 'tau': [0.6, 0.6, 0.39999999999999997, 0.0, -0.7999999999999999, 0.6],
 'rho': [0.7,
  0.7,
  0.49999999999999994,
  -0.09999999999999999,
  -0.8999999999999998,
  0.7999999999999999]}

### Show results

In [152]:
correlation_with_true_rankings= pd.DataFrame.from_dict(correlation_with_true_rankings)
correlation_with_true_rankings.index = ['obs_closed_form', 'caus_closed_form', 'random', 'sample size', 'similarity_cov_distrib_ranking', 'similarity_pscore_ranking size'] #, 'obs_from_samples', 'caus_from_samples']
correlation_with_true_rankings

precision_at_1  precision_at_3  \
obs_closed_form                            0.0        1.000000   
caus_closed_form                           0.0        1.000000   
random                                     0.0        0.333333   
sample size                                0.0        0.666667   
similarity_cov_distrib_ranking             0.0        0.333333   
similarity_pscore_ranking size             0.0        1.000000   

                                precision_at_5  tau  rho  
obs_closed_form                            1.0  0.6  0.7  
caus_closed_form                           1.0  0.6  0.7  
random                                     0.8  0.4  0.5  
sample size                                0.8  0.0 -0.1  
similarity_cov_distrib_ranking             1.0 -0.8 -0.9  
similarity_pscore_ranking size             1.0  0.6  0.8

### GP EIG


In [153]:
cGP = CausalGP()
X_host = host.drop(columns=["Y","T"]).iloc[:,:causal_param_first_index].values
T_host = host["T"].values.astype(int)
Y_host = host["Y"].values
cGP.fit(X_host,T_host,Y_host)

In [154]:
eig_results

{'EIG_obs_GP': [],
 'EIG_caus_GP': [],
 'EIG_obs_closed_form': [29.525043881803782,
  26.241507917969695,
  28.86417022989512,
  39.25597380738497,
  32.434968999432684],
 'EIG_caus_closed_form': [13.277509889220699,
  10.05399132026421,
  11.660204166263345,
  19.28841451878147,
  17.137688299526964],
 'EIG_obs_bart': [],
 'EIG_caus_bart': []}

In [155]:
for _, candidate in candidate_sites.items():
    X_cand = candidate.drop(columns=["Y","T"]).iloc[:,:causal_param_first_index].values
    T_cand = candidate["T"].values.copy()
    cGP.obs_EIG_closed_form(X_cand,T_cand)
    eig_results["EIG_obs_GP"].append(
             cGP.obs_EIG_closed_form(X_cand,T_cand)
            )
    eig_results["EIG_caus_GP"].append(
             cGP.causal_EIG_closed_form(X_cand,T_cand)
            )

In [156]:
X_cand = candidate.drop(columns=["Y","T"]).iloc[:,:causal_param_first_index].values
T_cand = candidate["T"].values.copy()

In [157]:
eig_results["EIG_obs_GP"],eig_results["EIG_caus_GP"]

([34.38349234565071,
  30.385176360556677,
  33.36763140349907,
  47.30178313275441,
  42.40523602171806],
 [10.65074259129591,
  8.790110003557515,
  9.97424823844699,
  14.797216400608391,
  11.4799342192361])

In [158]:
obs_eig_ranking_closed_form_GP = sorted(range(len(eig_results["EIG_obs_GP"])), key=lambda i: eig_results["EIG_obs_GP"][i], reverse=True)
print(obs_eig_ranking_closed_form)

caus_eig_ranking_closed_form_GP = sorted(range(len(eig_results["EIG_caus_GP"])), key=lambda i: eig_results["EIG_caus_GP"][i], reverse=True)
print(caus_eig_ranking_closed_form)

[3, 4, 0, 2, 1]
[3, 4, 0, 2, 1]


In [159]:
X_host_test = host_test.drop(columns=["Y","T"]).iloc[:,:causal_param_first_index].values

merged_mse_GP = []
for i, candidate in merged_datasets.items():

    X_merged = candidate.drop(columns=["Y","T"]).iloc[:,:causal_param_first_index].values
    T_merged = candidate["T"].values.astype(int)
    Y_merged = candidate["Y"].values
    cGP_new = CausalGP()

    cGP_new.fit(X_merged,T_merged,Y_merged)


    true_cate = (X_one - X_zero) @ beta

    pred_cate = cGP_new.pred_CATE(X_host_test)

    merged_mse_GP.append(mean_squared_error(true_cate, pred_cate))

In [160]:
true_cate_ranking_GP = sorted(range(len(merged_mse_GP)), key=lambda i: merged_mse_GP[i], reverse=False) # reverse is False because its error terms

In [161]:
true_cate_ranking_GP = sorted(range(len(merged_mse_GP)), key=lambda i: merged_mse_GP[i], reverse=False) # reverse is False because its error terms

In [162]:
len(obs_eig_ranking_closed_form_GP)

5

In [163]:
true_cate_ranking_GP

[2, 0, 3, 1, 4]

In [164]:
kendalltau(true_cate_ranking,true_cate_ranking_GP)

SignificanceResult(statistic=-0.19999999999999998, pvalue=0.8166666666666667)

In [165]:
obs_eig_ranking_closed_form_GP

[3, 4, 0, 2, 1]

In [166]:
# correlation_with_true_rankings_GP = {}
# compare_to_ground_truth(correlation_with_true_rankings_GP, true_cate_ranking_GP, obs_eig_ranking_closed_form_GP,merged_mse=merged_mse_GP, top_n = top_n, k = k)
# compare_to_ground_truth(correlation_with_true_rankings_GP, true_cate_ranking_GP, caus_eig_ranking_closed_form_GP,merged_mse=merged_mse_GP, top_n = top_n, k = k)

In [167]:
X = candidate.drop(columns=["Y","T"]).iloc[:,:causal_param_first_index].values
T = candidate["T"].values.astype(int).copy()

In [168]:
###### below is version where ground truth is wrt merged dataset

# for i, candidate in merged_datasets.items():

#     XandT_merged = candidate.drop(columns=["Y"])
#     Y_merged = candidate['Y']

#     learner = LinearRegression(fit_intercept=False)
#     learner.fit(y=Y_merged, X=XandT_merged) # we fit on merged datasets

#     true_cate = data_with_groundtruth.loc[XandT_merged.index, 'ite']

#     X_zero = XandT_merged.copy() # we predict on host with T=0 and T=1
#     X_zero.iloc[:,causal_param_first_index:] = 0

#     X_one = XandT_merged.copy()
#     X_one.iloc[:,causal_param_first_index:] = XandT_merged.iloc[:,:causal_param_first_index]

#     pred_cate = learner.predict(X_one)-learner.predict(X_zero)

#     merged_mse.append(mean_squared_error(true_cate, pred_cate))

## bart stuff

In [169]:
# X_host, T_host, Y_host = host.drop(columns=['T','Y']).values, host['T'].values.astype(np.int32), host['Y'].values

# prior_hyperparameters = {'sigma_0_sq':1, 'p_categorical_pr':0, 'p_categorical_trt':0 }
# predictive_model_parameters={"num_trees_pr":200,"num_trees_trt":100}
# conditional_model_param={"num_trees_pr":200}


# for i, candidate in candidate_sites.items():

#     print("from samples "+str(i))
#     X_cand, T_cand = candidate.drop(columns=['Y','T']).values, candidate['T'].values.astype(np.int32)

#     bcf = BayesianCausalForest(
#         prior_hyperparameters,
#         predictive_model_parameters=predictive_model_parameters,
#         conditional_model_param=conditional_model_param)
#     bcf.store_train_data(X=X_host, T=T_host, Y=Y_host)
    
#     joint_eig = bcf.joint_EIG_calc(X_cand, T_cand, sampling_parameters)

#     results["EIG_obs_bart"].append(joint_eig["Obs EIG"])
#     results["EIG_caus_bart"].append(joint_eig["Causal EIG"])

In [170]:
NUM_TREES_PR = 200
NUM_TREES_TRT = 100

In [183]:
predictive_model_parameters = {"parallel":True, 
    "burnin":15,
    "max_depth":250,
    "num_trees_pr":NUM_TREES_PR,
    "num_trees_trt":NUM_TREES_TRT,
    "num_cutpoints":100,
    "Nmin":1,
    #mtry_pr=X1.shape[1], # default 0 seems to be 'all'
    #mtry_trt=X.shape[1], 
    "tau_pr" : 0.6 * np.var(Y_host)/NUM_TREES_PR, #0.6 * np.var(y) / /NUM_TREES_PR,
    "tau_trt" : 0.1 * np.var(Y_host)/NUM_TREES_TRT, #0.1 * np.var(y) / /NUM_TREES_TRT,
    "alpha_pr": 0.95, # shrinkage (splitting probability)
    "beta_pr" : 2, # shrinkage (tree depth)
    "alpha_trt" : 0.95, # shrinkage for treatment part
    "beta_trt" : 2,
    "standardize_target" : True,
    "parallel":True}

In [184]:
bcf = BayesianCausalForest(prior_hyperparameters = {'sigma_0_sq':1, 'p_categorical_pr':0, 'p_categorical_trt':0 },predictive_model_parameters=predictive_model_parameters,conditional_model_param={"num_trees_pr":200})

In [185]:
bcf.store_train_data(X=X_host,Y=Y_host,T=T_host.astype(np.int32))

In [186]:
X_host_test
T_host_test = np.array(host_test["T"]).astype(np.int32)

In [187]:
X_host_test.shape

(2000, 76)

In [188]:
predictions,tau = bcf.posterior_sample_predictions(X_host_test,T_host_test,500,True)

In [189]:
np.array(host_test["Y"])

array([ 7.33611433,  5.47923491, -4.14439838, ..., 12.54454834,
        4.56450127,  0.88572355])

In [190]:
predictions.mean(axis=0)

array([ 5.78961881,  4.89740576, -2.16916045, ..., 10.97857034,
        4.33463969,  1.11830411])

In [191]:
mean_squared_error(predictions.mean(axis=0),np.array(host_test["Y"]))

2.76961153299505

In [192]:
tau.mean(axis=0)

array([-1.23595698, -1.32307062, -7.9694842 , ..., -1.2498779 ,
       -7.84716551, -6.11784233])

In [193]:
bcf.model.predict(X_host_test)

array([-1.25333239, -1.32235605, -7.96158688, ..., -1.24329455,
       -7.85945692, -6.12691146])

In [194]:
mean_squared_error(true_cate,bcf.model.predict(X_host_test))

1.9071233373433976

In [195]:
mean_squared_error(true_cate,cGP.pred_CATE(X_host_test))

0.5689872746518924

In [196]:
tau = tau.T

In [197]:
np.argmax((np.array(true_cate)-tau.mean(axis=0))**2 )

ValueError: operands could not be broadcast together with shapes (2000,) (500,) 

In [ ]:
np.array(true_cate)[1773]

0.3289473684210531

In [ ]:
((np.array(true_cate)-tau.mean(axis=0))**2)[1773]

0.05886216381907854

In [ ]:
(np.array(true_cate)-tau.mean(axis=0))[533]

-2.2418758900052587

In [ ]:
true_cate.max()

9.664473684210526

In [ ]:
tau.mean(axis=0).min()

-0.7784898309015698

In [ ]:
((true_cate-tau.mean(axis=0)))**2

5919      1.591757
10966     1.922574
10174     0.019214
6031      0.019269
4146      1.214158
           ...    
11757     1.942427
9074     10.870195
6406      0.345829
8591      1.613102
6907      3.940041
Length: 2000, dtype: float64

In [ ]:
bcf.model.predict(X_host_test).max()

array([-0.38428833, -0.19764936,  0.39700604, ...,  0.29465884,
        0.13820728,  0.54172922])

In [ ]:
mean_squared_error(true_cate)

TypeError: missing a required argument: 'y_pred'

In [ ]:
mean_squared_error(true_cate,cGP.pred_CATE(X_host_test))

0.7531781778947065